# Load Stuff

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
import pandas as pd
import numpy as np
import imageio
import matplotlib.pyplot as plt
import bs4
import requests
import time
import pickle
import seaborn as sns
import matplotlib.pyplot as plt
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import OrdinalEncoder
from collections import Counter
from textblob import TextBlob
import nltk

nltk.download('all')
nltk.download('punkt')

!pip install fuzzywuzzy[speedup]
import fuzzywuzzy
from fuzzywuzzy import fuzz
from fuzzywuzzy import process

myCars = pd.read_csv("/content/drive/MyDrive/car_data.csv", low_memory=False)
scaler = StandardScaler()

[nltk_data] Downloading collection 'all'
[nltk_data]    | 
[nltk_data]    | Downloading package abc to /root/nltk_data...
[nltk_data]    |   Unzipping corpora/abc.zip.
[nltk_data]    | Downloading package alpino to /root/nltk_data...
[nltk_data]    |   Unzipping corpora/alpino.zip.
[nltk_data]    | Downloading package biocreative_ppi to
[nltk_data]    |     /root/nltk_data...
[nltk_data]    |   Unzipping corpora/biocreative_ppi.zip.
[nltk_data]    | Downloading package brown to /root/nltk_data...
[nltk_data]    |   Unzipping corpora/brown.zip.
[nltk_data]    | Downloading package brown_tei to /root/nltk_data...
[nltk_data]    |   Unzipping corpora/brown_tei.zip.
[nltk_data]    | Downloading package cess_cat to /root/nltk_data...
[nltk_data]    |   Unzipping corpora/cess_cat.zip.
[nltk_data]    | Downloading package cess_esp to /root/nltk_data...
[nltk_data]    |   Unzipping corpora/cess_esp.zip.
[nltk_data]    | Downloading package chat80 to /root/nltk_data...
[nltk_data]    |   Unzipp

In [ ]:
# Load data (deserialize)
with open('/pickles/entDict.pickle', 'rb') as handle:
    entDict = pickle.load(handle)

with open('/pickles/extDict.pickle', 'rb') as handle:
    extDict = pickle.load(handle)
  
with open('/pickles/intDict.pickle', 'rb') as handle:
    intDict = pickle.load(handle)
  
with open('/pickles/mechDict.pickle', 'rb') as handle:
    mechDict = pickle.load(handle)
  
with open('/pickles/safeDict.pickle', 'rb') as handle:
    safeDict = pickle.load(handle)

# Main Column Cleaning

In [ ]:
def columChecker(df, string):
  print(df[string].value_counts())
  print()
  print(df[string].describe())
  print("Are there nans?")
  print(df[string].isnull().values.any())
  print()
  plt.figure(figsize=(10,15))
  sns.scatterplot(x=df[string],y=df["Starting MSRP"].astype(float)/10000)
  plt.show()

In [ ]:
# Super usefull found on stack overflow https://stackoverflow.com/questions/37292872/how-can-i-one-hot-encode-in-python
def encode_and_bind(original_dataframe, feature_to_encode):
    dummies = pd.get_dummies(original_dataframe[[feature_to_encode]])
    res = pd.concat([original_dataframe, dummies], axis=1)
    res = res.drop([feature_to_encode], axis=1)
    return(res) 

Ran info(verbose=True, null_counts=True) to check nan's in data frame removed completly empty columns from the data frame.

All dropped columns here: (including those we decided to drop later)

In [ ]:
myCars["Starting MSRP"] = myCars["Starting MSRP"].str.strip("\n$").str.rstrip(" \n").str.replace(",","").astype(int)

In [ ]:
myCars["Doors"] = myCars["Doors"].str.rstrip("-door").astype(int)

In [ ]:
myCars["Seats"] = myCars["Seats"].str.rstrip("seats").astype(float)

Checked and Front and rear wheel material always match so made a single column to indicate wheel material, and removed front and rear wheel material columns.

In [ ]:
myCars["Wheel Material"] = myCars["Front Wheel Material"] 
myCars=myCars.drop(columns=["Front Wheel Material","Rear Wheel Material"])

I commented these out because I didn't want to deal with all the extra columns... For now I have just been cleaning the numerical columns, figured we can encode or do whatever else needs to be done with the categorical stuff after wards.

In [ ]:
#filling NaN's for "Cold Cranking Amps @ 0° F (Primary)", 
myCars["Cold Cranking Amps @ 0° F (Primary)"].fillna("-1", inplace=True)
myCars["Maximum Alternator Capacity (amps)"].fillna("-1", inplace=True)
myCars["Reverse Ratio (:1)"].fillna("-1", inplace=True)
myCars["Reverse Ratio (:1)"] = myCars["Reverse Ratio (:1)"].astype(float)
myCars["Maximum Alternator Capacity (amps)"] = myCars["Maximum Alternator Capacity (amps)"].astype(float)
myCars["Cold Cranking Amps @ 0° F (Primary)"] = myCars["Cold Cranking Amps @ 0° F (Primary)"].astype(float)

In [ ]:
#I removed the inner for-loop after I realized what was going on. This should be more efficient than the first one I sent you
roomNames = []

#Pulls out the second and first room features. Use 'roomNames to see the list
for roomFeatures in myCars.columns:
  if 'Room' in roomFeatures:
    word = roomFeatures
    if 'Second' in word:
      roomNames.append(roomFeatures)
    elif 'Front' in word:
      roomNames.append(roomFeatures)

#Clean all the rows, convert NA to 0 and entire columns to floats.
for row in roomNames:
  myCars[row] = myCars[row].str.replace(" ", "").str.replace("N/A", "-1")
  myCars[row] = myCars[row].str.replace("in", "").astype(float)

In [ ]:
#cleaned and then one hot encoded "Engine Oil Cooler"
myCars["Engine Oil Cooler"] = myCars["Engine Oil Cooler"].replace("None",-1)

In [ ]:
#cleaned and then one hot encoded "Transfer Case Model"
myCars["Transfer Case Model"] = myCars["Transfer Case Model"].replace("None",-1)

In [ ]:
myCars["Engine Type"][0]

'Gas/Electric V-6'

In [ ]:
#creating a column based on engine type to specify whether cars are gas (0), hybrid (1), or electric (2)
energyType=np.zeros(len(myCars))

for i in range(len(myCars)):
  if 'electric' in myCars["Engine Type"][i].lower():
    energyType[i]=energyType[i]+2
    if 'gas' in myCars["Engine Type"][i].lower():
      energyType[i]=energyType[i]-1

myCars["Energy Type"]=energyType

myCars["Energy Type"].value_counts()



0.0    2052
1.0     320
2.0      60
Name: Energy Type, dtype: int64

In [ ]:
#All of the "EPA MPG Equivalent" rows with values had "EPA Fuel Economy" with "N/A"'s so I filled the holes in "EPA fuel economy" with the data 
#from the other column. After swapping all the data over I dropped the "EPA MPG Equivalent columns" 
epaCity2 = myCars["EPA MPG Equivalent - City"]
epaHwy2 = myCars["EPA MPG Equivalent - Hwy"]
epaComb2 = myCars["EPA MPG Equivalent - Combined"]
for i in range(0,2429):
  if "N/A" in myCars["EPA Fuel Economy Est - City"][i]:
    if np.isnan(epaCity2[i]) == False:
      myCars["EPA Fuel Economy Est - City"][i] = epaCity2[i].astype(str)
    else:
      myCars["EPA Fuel Economy Est - City"][i] = "-1"
  if "N/A" in myCars["EPA Fuel Economy Est - Hwy"][i]:
    if np.isnan(epaHwy2[i]) == False:
      myCars["EPA Fuel Economy Est - Hwy"][i] = epaHwy2[i].astype(str)
    else:
      myCars["EPA Fuel Economy Est - Hwy"][i] = "-1"
  if "N/A" in myCars["Fuel Economy Est-Combined"][i]:
    if np.isnan(epaComb2[i]) == False:
      myCars["Fuel Economy Est-Combined"][i] = epaComb2[i].astype(str)
    else:
      myCars["Fuel Economy Est-Combined"][i] = "-1"


myCars["EPA Fuel Economy Est - City"] = myCars["EPA Fuel Economy Est - City"].str.rstrip("MPG").str.replace("\(Est\)","").str.replace("\(2020\)","").str.replace(" ","")
myCars["EPA Fuel Economy Est - Hwy"] = myCars["EPA Fuel Economy Est - Hwy"].str.rstrip("MPG").str.replace("\(2020\)","").str.replace("\(Est\)","").str.replace(" ","")
myCars["Fuel Economy Est-Combined"] = myCars["Fuel Economy Est-Combined"].str.rstrip("MPG").str.replace("\(2020\)","").str.replace("\(Est\)","").str.replace(" ","")

myCars["EPA Fuel Economy Est - City"] =myCars["EPA Fuel Economy Est - City"].astype(float)
myCars["EPA Fuel Economy Est - Hwy"] =myCars["EPA Fuel Economy Est - Hwy"].astype(float)
myCars["Fuel Economy Est-Combined"] =myCars["Fuel Economy Est-Combined"].astype(float)

myCars=myCars.drop(columns=["EPA MPG Equivalent - City","EPA MPG Equivalent - Hwy","EPA MPG Equivalent - Combined"]);

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  if __name__ == '__main__':
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:11: SettingWithCopyW

In [ ]:
#Splitting rear wheel size:
myCars["Rear Wheel Size"] = myCars["Rear Wheel Size"].str.replace('x', 'X')
rearSplit = myCars["Rear Wheel Size"].str.split("X", n = 1, expand = True)
myCars["Rear Wheel Diameter (in)"] = rearSplit[0].str.replace("\"","").astype(float)
cleanR = rearSplit[1].str.replace("in", "").str.replace("\"", "").str.replace(" ", "").str.replace("-TBD-", "-1").astype(float)
myCars["Rear Wheel Width (in)"] = cleanR

#Splitting front wheel size:
myCars["Front Wheel Size"] = myCars["Front Wheel Size"].str.replace('x', 'X')
frontSplit = myCars["Front Wheel Size"].str.split("X", n = 1, expand = True)
myCars["Front Wheel Diameter (in)"] = frontSplit[0].str.replace("\"","").astype(float)
cleanF = frontSplit[1].str.replace("in", "").str.replace("\"", "").str.replace(" ", "").str.replace("-TBD-", "-1").astype(float)
myCars["Front Wheel Width (in)"] = cleanF

#drop the front and rear wheel size
myCars = myCars.drop(columns=["Rear Wheel Size","Front Wheel Size" ])

In [ ]:
#displacment
front = myCars["Displacement"].str.split("/", n =0, expand=True)[0]
myCars["Displacement (L)"] = front.str.replace(" ", "").str.replace("L", "").astype(float)
myCars=myCars.drop(columns=["Displacement"])

In [ ]:
#Cleaning torque. Values are in foot lbs!
store = myCars["SAE Net Torque @ RPM"].str.split("@", n =0, expand=True)[0]
myCars["Torque (Ft lbs)"] = store.str.replace(" ", "").astype(float)

#Cleaning horsepower
store = myCars["SAE Net Horsepower @ RPM"].str.split("@", n =0, expand=True)[0]
myCars["Horsepower"] = store.str.replace(" ", "").astype(float)

#dropping the columms:
myCars = myCars.drop(columns=["SAE Net Torque @ RPM","SAE Net Horsepower @ RPM" ])

In [ ]:
#cleans all gear ratios
gears = []

for i in myCars.columns:
  if "Gear Ratio" in i:
    gears.append(i)

for gear in gears:
  column = myCars[gear].astype(str)
  for leng in range(len(column)):
    if "-" in column[leng]:
      num1 = column[leng].split("-")[0]
      num2 = column[leng].split("-")[1]
      storeVal = float(num1) - float(num2)
      myCars[gear][leng] = storeVal
  mean = myCars[gear].astype(float).mean()
  myCars[gear].fillna(mean, inplace=True)

myCars["First Gear Ratio (:1)"]=myCars["First Gear Ratio (:1)"].astype(float);  #this was being left as an object for whatever reason
myCars["Final Drive Axle Ratio (:1)"]=myCars["Final Drive Axle Ratio (:1)"].fillna(-1)

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  from ipykernel import kernelapp as app


In [ ]:
#cargo volume columns for seat rows 1-4
myCars["Cargo Volume to Seat 1"].fillna("N/A", inplace=True)
myCars["Cargo Volume to Seat 2"].fillna("N/A", inplace=True)
myCars["Cargo Volume to Seat 3"].fillna("N/A", inplace=True)
myCars["Cargo Volume to Seat 4"].fillna("N/A", inplace=True)

myCars["Cargo Volume to Seat 1"] = myCars["Cargo Volume to Seat 1"].str.replace("ft³", "").str.replace(" ", "").str.replace("N/A", "-1").astype(float)
myCars["Cargo Volume to Seat 2"] = myCars["Cargo Volume to Seat 2"].str.replace("ft³", "").str.replace(" ", "").str.replace("N/A", "-1").astype(float)
myCars["Cargo Volume to Seat 3"] = myCars["Cargo Volume to Seat 3"].str.replace("ft³", "").str.replace(" ", "").str.replace("N/A", "-1").astype(float)
myCars["Cargo Volume to Seat 4"] = myCars["Cargo Volume to Seat 4"].str.replace("ft³", "").str.replace(" ", "").str.replace("N/A", "-1").astype(float)

In [ ]:
#cleaned cargo area
myCars["Cargo Area Length @ Floor to Seat 3"].fillna("N/A", inplace=True)
myCars["Cargo Area Length @ Floor to Seat 2"].fillna("N/A", inplace=True)
myCars["Cargo Area Width @ Beltline"].fillna("N/A", inplace=True)
myCars["Cargo Area Length @ Floor to Seat 1"].fillna("N/A", inplace=True)

myCars["Cargo Area Length @ Floor to Seat 3"] = myCars["Cargo Area Length @ Floor to Seat 3"].str.replace("in", "").str.replace(" ", "").str.replace("N/A", "-1").astype(float)
myCars["Cargo Area Length @ Floor to Seat 2"] = myCars["Cargo Area Length @ Floor to Seat 2"].str.replace("in", "").str.replace(" ", "").str.replace("N/A", "-1").astype(float)
myCars["Cargo Area Width @ Beltline"] = myCars["Cargo Area Width @ Beltline"].str.replace("in", "").str.replace(" ", "").str.replace("N/A", "-1").astype(float)
myCars["Cargo Area Length @ Floor to Seat 1"] = myCars["Cargo Area Length @ Floor to Seat 1"].str.replace("in", "").str.replace(" ", "").str.replace("N/A", "-1").astype(float)
myCars["Cargo Area Length @ Floor to Seat 3"] = myCars["Cargo Area Length @ Floor to Seat 3"].astype(float)

In [ ]:
#fuel tank capacity
myCars["Fuel Tank Capacity, Approx"] = myCars["Fuel Tank Capacity, Approx"].str.replace(" gal","").str.replace("N/A","-1").astype(float)
myCars["Fuel Tank Capacity, Approx (gal)"]=myCars["Fuel Tank Capacity, Approx"]
myCars=myCars.drop(columns=["Fuel Tank Capacity, Approx"])

In [ ]:
#trans type
myCars["Trans Type"]=myCars["Trans Type"].astype(int)

In [ ]:
#front brake rotor diam x thickness
fb_rotor_diam=[]

for x in myCars["Front Brake Rotor Diam x Thickness"]:
    split=x.split('x')
    if len(split)>=1:
      fb_rotor_diam.append(split[0])
    else:
      fb_rotor_diam=fb_rotor_diam.append('')

myCars["Front Brake Rotor Diam (in)"]=fb_rotor_diam
myCars["Front Brake Rotor Diam (in)"]=myCars["Front Brake Rotor Diam (in)"].str.replace(" in","").str.replace("N/A","-1").astype(float)

#rear brake rotor diam x thickness
rb_rotor_diam=[]

for x in myCars["Rear Brake Rotor Diam x Thickness"]:
    split=x.split('x')
    if len(split)>=1:
      rb_rotor_diam.append(split[0])
    else:
      rb_rotor_diam=fb_rotor_diam.append('')

myCars["Rear Brake Rotor Diam (in)"]=rb_rotor_diam
myCars["Rear Brake Rotor Diam (in)"]=myCars["Rear Brake Rotor Diam (in)"].str.replace(" in","").str.replace("N/A","-1").astype(float)

#dropping old columns
myCars=myCars.drop(columns=["Front Brake Rotor Diam x Thickness","Rear Brake Rotor Diam x Thickness"])

In [ ]:
#turning diameter
myCars["Turning Diameter - Curb to Curb"]=myCars["Turning Diameter - Curb to Curb"].str.replace(" ft","").str.replace("N/A","-1").astype(float)

In [ ]:
compactIn = np.zeros(2432)

for i in range(0, 2431):
  if "Compact in" in myCars["Spare Wheel Size"][i]:
    compactIn[i] = 1
  if "Full-Size in" in myCars["Spare Wheel Size"][i]:
    myCars["Spare Wheel Size"][i] = myCars["Front Tire Size"][i]
myCars["Compact in Spare Tire"]  = compactIn
myCars["Spare Wheel Size"] = myCars["Spare Wheel Size"].str.replace("Compact in", "0.0").str.replace("N/A", "0.0")


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  import sys


In [ ]:
#front tires
ft_width=[]
ft_ar=[]
ft_rd=[]

for x in myCars["Front Tire Size"]:
  split=x.split("/")
  ft_width.append(int(split[0][len(split[0])-3:]))
  ft_ar.append(int(split[1][:2]))
  rd=''
  for char in split[1][2:]:
    if not char.isalpha():
      rd=rd+char
  ft_rd.append(float(rd))

myCars["Front Tire Width (mm)"]=ft_width
myCars["Front Tire Aspect Ratio (%)"]=ft_ar
myCars["Front Tire Rim Diameter (in)"]=ft_rd

#rear tires
rt_width=[]
rt_ar=[]
rt_rd=[]

for x in myCars["Rear Tire Size"]:
  split=x.split("/")
  rt_width.append(int(split[0][len(split[0])-3:]))
  rt_ar.append(int(split[1][:2]))
  rd=''
  for char in split[1][2:]:
    if not char.isalpha():
      rd=rd+char
  rt_rd.append(float(rd))

myCars["Rear Tire Width (mm)"]=rt_width
myCars["Rear Tire Aspect Ratio (%)"]=rt_ar
myCars["Rear Tire Rim Diameter (in)"]=rt_rd

#dropping
myCars=myCars.drop(columns=["Rear Tire Size","Front Tire Size"])

In [ ]:
#trailer stuff
myCars["Wt Distributing Hitch - Max Trailer Wt. (lbs)"]=myCars["Wt Distributing Hitch - Max Trailer Wt."].str.replace(" lbs","").str.replace("N/A","-1").astype(float)
myCars["Dead Weight Hitch - Max Trailer Wt. (lbs)"]=myCars["Dead Weight Hitch - Max Trailer Wt."].str.replace(" lbs","").str.replace("N/A","-1").astype(float)
myCars["Wt Distributing Hitch - Max Tongue Wt. (lbs)"]=myCars["Wt Distributing Hitch - Max Tongue Wt."].str.replace(" lbs","").str.replace("N/A","-1").astype(float)
myCars["Dead Weight Hitch - Max Tongue Wt. (lbs)"]=myCars["Dead Weight Hitch - Max Tongue Wt."].str.replace(" lbs","").str.replace("N/A","-1").astype(float)
myCars["Maximum Trailering Capacity (lbs)"]=myCars["Maximum Trailering Capacity"].str.replace(" lbs","").str.replace("N/A","-1").astype(float)

myCars=myCars.drop(columns=["Wt Distributing Hitch - Max Trailer Wt.","Dead Weight Hitch - Max Trailer Wt.","Wt Distributing Hitch - Max Tongue Wt.","Dead Weight Hitch - Max Tongue Wt.","Maximum Trailering Capacity"])

In [ ]:
#gross axle weight rating
myCars["Gross Axle Weight Rating (lbs)"]=myCars["Gross Axle Weight Rating"].str.replace(" lbs","").str.replace("N/A","-1").astype(float)
myCars=myCars.drop(columns=["Gross Axle Weight Rating"])

In [ ]:
#weight stuff
myCars["Curb Weight - Rear (lbs)"]=myCars["Curb Weight - Rear"].str.replace(" lbs","").str.replace("N/A","-1").astype(float)
myCars["Gross Vehicle Weight Rating (lbs)"]=myCars["Gross Vehicle Weight Rating"].str.replace(" lbs","").astype(float)
myCars["Gross Combined Wt Rating (lbs)"]=myCars["Gross Combined Wt Rating"].str.replace(" lbs","").str.replace("N/A","-1").astype(float)
myCars["Curb Weight - Front (lbs)"]=myCars["Curb Weight - Front"].str.replace(" lbs","").str.replace("N/A","-1").astype(float)
myCars["Curb Weight (lbs)"]=myCars["Curb Weight"].str.replace(" lbs","").str.replace("N/A","-1").astype(float)
myCars["Payload (lbs)"]=myCars["As Spec'd Payload"].str.replace(" lbs","").str.replace("N/A","-1").astype(float)
myCars["Base Curb Weight (lbs)"]=myCars["Base Curb Weight"].str.replace(" lbs","").str.replace("N/A","-1").astype(float)
myCars["Maximum Payload Capacity (lbs)"]=myCars["Maximum Payload Capacity"].str.replace(" lbs","").str.replace("N/A","-1").astype(float)

myCars=myCars.drop(columns=["Curb Weight - Rear","Gross Vehicle Weight Rating","Gross Combined Wt Rating","Curb Weight - Front","Curb Weight","As Spec'd Payload","Base Curb Weight","Maximum Payload Capacity"])

In [ ]:
#dimensions and stuff
myCars["Wheelbase (in)"]=myCars["Wheelbase"].str.replace(" in","").str.replace("N/A","-1").astype(float)
myCars["Ground Clearance, Rear (in)"]=myCars["Ground Clearance, Rear"].str.replace(" in","").str.replace("N/A","-1").astype(float)
myCars["Height, Overall (in)"]=myCars["Height, Overall"].str.replace(" in","").str.replace("N/A","-1").astype(float)
myCars["Cargo Box Width @ Wheelhousings (in)"]=myCars["Cargo Box Width @ Wheelhousings"].str.replace(" in","").str.replace("N/A","-1").astype(float)
myCars["Cargo Box Width @ Floor (in)"]=myCars["Cargo Box Width @ Floor"].str.replace(" in","").str.replace("N/A","-1").astype(float)
myCars["Ground to Top of Load Floor (in)"]=myCars["Ground to Top of Load Floor"].str.replace(" in","").str.replace("N/A","-1").astype(float)
myCars["Length, Overall (in)"]=myCars["Length, Overall"].str.replace(" in","").str.replace("N/A","-1").astype(float)
myCars["Tailgate Width (in)"]=myCars["Tailgate Width"].str.replace(" in","").str.replace("N/A","-1").astype(float)
myCars["Ground Clearance, Front (in)"]=myCars["Ground Clearance, Front"].str.replace(" in","").str.replace("N/A","-1").astype(float)
myCars["Cargo Box (Area) Height (in)"]=myCars["Cargo Box (Area) Height"].str.replace(" in","").str.replace("N/A","-1").astype(float)
myCars["Cargo Box Width @ Top, Rear (in)"]=myCars["Cargo Box Width @ Top, Rear"].str.replace(" in","").str.replace("N/A","-1").astype(float)
myCars["Width, Max w/o mirrors (in)"]=myCars["Width, Max w/o mirrors"].str.replace(" in","").str.replace("N/A","-1").astype(float)
myCars["Overhang, Front (in)"]=myCars["Overhang, Front"].str.replace(" in","").str.replace("N/A","-1").astype(float)
myCars["Cargo Volume (ft^3)"]=myCars["Cargo Volume"].str.replace(" ft³","").str.replace("N/A","-1").astype(float)
myCars["Cargo Box Length @ Floor (in)"]=myCars["Cargo Box Length @ Floor"].str.replace(" in","").str.replace("N/A","-1").astype(float)
myCars["Min Ground Clearance (in)"]=myCars["Min Ground Clearance"].str.replace(" in","").str.replace("N/A","-1").astype(float)
myCars["Passenger Volume (ft^3)"]=myCars["Passenger Volume"].str.replace(" ft³","").str.replace("N/A","-1").astype(float)
myCars["Trunk Volume (ft^3)"]=myCars["Trunk Volume"].str.replace(" ft³","").str.replace("N/A","-1").astype(float)
myCars["Track Width, Front (in)"]=myCars["Track Width, Front"].str.replace(" in","").str.replace("N/A","-1").astype(float)
myCars["Liftover Height (in)"]=myCars["Liftover Height"].str.replace(" in","").str.replace("N/A","-1").astype(float)
myCars["Track Width, Rear (in)"]=myCars["Track Width, Rear"].str.replace(" in","").str.replace("N/A","-1").astype(float)

myCars=myCars.drop(columns=["Wheelbase","Ground Clearance, Rear","Height, Overall","Cargo Box Width @ Wheelhousings","Cargo Box Width @ Floor","Ground to Top of Load Floor",
                            "Length, Overall","Tailgate Width","Ground Clearance, Front","Cargo Box (Area) Height","Cargo Box Width @ Top, Rear","Width, Max w/o mirrors","Overhang, Front",
                            "Cargo Volume","Cargo Box Length @ Floor","Min Ground Clearance","Passenger Volume","Trunk Volume","Track Width, Front","Liftover Height","Track Width, Rear"])

In [ ]:
#this code checks how many seat rows a car has data for by checking if there is head space data for each car row. 5th row is not included
#because apparentlly there is not 5th row data it's all "N/A"'s
seatRows = np.ones(2432, dtype=str)
myCars["Third Head Room"].fillna("N/A", inplace=True)
myCars["Fourth Head Room"].fillna("N/A", inplace=True)
myCars["Fourth Head Room"].fillna("N/A", inplace=True)

for i in range(len(myCars)):
   if not myCars["Front Head Room"][i]=='N/A':
    seatRows[i] = "1"
   if not myCars["Second Head Room"][i]=='N/A':
     seatRows[i] = "2"
   if not myCars["Third Head Room"][i]=='N/A':
     seatRows[i] = "3"
   if not myCars["Fourth Head Room"][i]=='N/A':
     seatRows[i] = "4"
myCars["Seat Rows"] = seatRows.astype(float)

myCars=myCars.drop(columns=["Third Head Room","Third Leg Room","Third Hip Room","Third Shoulder Room","Fourth Head Room","Fourth Shoulder Room",
                            "Fourth Leg Room","Fourth Hip Room","Fifth Shoulder Room","Fifth Hip Room","Fifth Leg Room","Fifth Head Room"])

In [ ]:
len(myCars["Exterior Color"][763].split('^^'))

7

In [ ]:
intColorCount=[]
extColorCount=[]

for i in range(len(myCars)):
  extColorCount.append(len(myCars["Exterior Color"][i].split('^^'))-1)
  intColorCount.append(len(myCars["Interior Color"][i].split('^^'))-1)

myCars["Ext Color Count"]=extColorCount
myCars["Int Color Count"]=intColorCount

In [ ]:
myCars.shape

(2432, 167)

# String Processing

This section includes both the code used to originally seperate out features and create features dictionaries as well as the code used to encode table values with those feature dictionaries.  Sections that are commented out are not relevant unless you are re-generating the feature dictionaries.

Cleans up the feature columns 

In [ ]:
# EntFeatCount = [] 
# ExtFeatCount = []
# IntFeatCount = []
# MechFeatCount = []
# SafeFeatCount = []

myCars['Entertainment Features'] = myCars['Entertainment Features'].str.replace("[","").str.replace("]","").str.replace("\"","").str.replace("\'","")
myCars['Exterior Features'] = myCars["Exterior Features"].str.replace("[","").str.replace("]","").str.replace("\"","").str.replace("\'","")
myCars['Interior Features'] = myCars["Interior Features"].str.replace("[","").str.replace("]","").str.replace("\"","").str.replace("\'","")
myCars['Mechanical Features'] = myCars['Mechanical Features'].str.replace("[","").str.replace("]","").str.replace("\"","").str.replace("\'","")
myCars['Safety Features'] = myCars['Safety Features'].replace("[","").str.replace("]","").str.replace("\"","").str.replace("\'","")

# for i in range (0, len(myCars)-1):
#   tempEntFeatCount = myCars['Entertainment Features'][i].split('^^,')
#   EntFeatCount = EntFeatCount + tempEntFeatCount

#   tempExtFeatCount = myCars['Exterior Features'][i].split('^^,')
#   ExtFeatCount = ExtFeatCount + tempExtFeatCount
  
#   tempIntFeatCount = myCars['Interior Features'][i].split('^^,')
#   IntFeatCount = IntFeatCount + tempIntFeatCount

#   tempMechFeatCount = myCars['Mechanical Features'][i].split('^^,')
#   MechFeatCount = MechFeatCount + tempMechFeatCount

#   tempSafeFeatCount = myCars['Safety Features'][i].split('^^,')
#   SafeFeatCount = tempSafeFeatCount + SafeFeatCount

# for i in range(len(EntFeatCount)):
#   EntFeatCount[i]=EntFeatCount[i].replace('^^','')
# for i in range(len(ExtFeatCount)):
#   ExtFeatCount[i]=ExtFeatCount[i].replace('^^','')
# for i in range(len(IntFeatCount)):
#   IntFeatCount[i]=IntFeatCount[i].replace('^^','')
# for i in range(len(MechFeatCount)):
#   MechFeatCount[i]=MechFeatCount[i].replace('^^','')
# for i in range(len(SafeFeatCount)):
#   SafeFeatCount[i]=SafeFeatCount[i].replace('^^','')

In [ ]:
#input list of features, output list of noun phrases
def blobify(featCount):
  features=[]
  for i in range(len(featCount)):
    text=TextBlob(featCount[i])
    features=features+text.noun_phrases
  return features

In [ ]:
#input list of noun phrases, list of unique elements (in descending order of avg. fuzz ratio), and dictionary
#replaces similar strings (reduces unique elements)
#adds replaced strings the dictionary with their replacements as an (old string, new string) tuple

def fuzzify(keys, featDict):
  done=[]
  for i in range(len(keys)):
    for x in range(i+1,len(keys)):
      if not(keys[x] in done):
        ratio=fuzz.ratio(keys[i],keys[x])
        if ratio>90:
          featDict[keys[x]]=keys[i]
          keys[x]=keys[i]
    done.append(keys[i])

In [ ]:
#takes list of noun phrases, adds dictionary entries to keyDict with (noun phrase, avg. fuzz.ratio score)
#fuzz.ratio average is calculated using all non-identical elements
#returns a list of unique elements from the inputed list
#an equal number of tuples are added to keyDict as are in the returned list (every unique value is given a dictionary entry)

def simCount(features,keyDict):
  finList=[]
  for i in range(len(features)):
    if not(features[i] in finList): 
      count=0
      for x in range(len(features)):
        ratio=fuzz.ratio(features[i],features[x])
        if not(features[i] in keyDict):
          keyDict[features[i]]=0
        if not(ratio==100):
          keyDict[features[i]]=keyDict[features[i]]+ratio
          count=count+1
      finList.append(features[i])
      keyDict[features[i]]=keyDict[features[i]]/count

In [ ]:
#input a dictionary with (string, float) tuples
#returns a list of strings in descending order of their corresponding float

def sortKeys(keyDict):
  allVals=[keyDict.get(k) for k in keyDict]
  sortedVals=sorted(allVals,reverse=True)
  orderedFeat=[list(keyDict.keys())[list(keyDict.values()).index(x)] for x in sortedVals]
  return orderedFeat

In [ ]:
# entKeyDict={}
# entDict={}

# entBlob=blobify(EntFeatCount)
# simCount(entBlob,entKeyDict)
# entKeySort=sortKeys(entKeyDict)
# fuzzify(entKeySort,entDict)

In [ ]:
# extKeyDict={}
# extDict={}

# extBlob=blobify(ExtFeatCount)
# simCount(extBlob,extKeyDict)
# extKeySort=sortKeys(extKeyDict)
# fuzzify(extKeySort,extDict)

In [ ]:
# intKeyDict={}
# intDict={}

# intBlob=blobify(IntFeatCount)
# simCount(intBlob,intKeyDict)
# intKeySort=sortKeys(intKeyDict)
# fuzzify(intKeySort,intDict)

In [ ]:
# mechKeyDict={}
# mechDict={}

# mechBlob=blobify(MechFeatCount)
# simCount(mechBlob,mechKeyDict)
# mechKeySort=sortKeys(mechKeyDict)
# fuzzify(mechKeySort,mechDict)

In [ ]:
# safeKeyDict={}
# safeDict={}

# safeBlob=blobify(SafeFeatCount)
# simCount(safeBlob,safeKeyDict)
# safeKeySort=sortKeys(safeKeyDict)
# fuzzify(safeKeySort,safeDict)

In [ ]:
# # Store data (serialize)
# with open('entDict.pickle', 'wb') as handle:
#     pickle.dump(entDict, handle, protocol=pickle.HIGHEST_PROTOCOL)
  
# with open('extDict.pickle', 'wb') as handle:
#     pickle.dump(extDict, handle, protocol=pickle.HIGHEST_PROTOCOL)

# with open('intDict.pickle', 'wb') as handle:
#     pickle.dump(intDict, handle, protocol=pickle.HIGHEST_PROTOCOL)

# with open('mechDict.pickle', 'wb') as handle:
#     pickle.dump(mechDict, handle, protocol=pickle.HIGHEST_PROTOCOL)

# with open('safeDict.pickle', 'wb') as handle:
#     pickle.dump(safeDict, handle, protocol=pickle.HIGHEST_PROTOCOL)

# from google.colab import drive
# drive.mount('/content/drive')
# # myCars.to_csv("cleanVehicleStats2.csv",index=False)
# !cp 'safeDict.pickle' "drive/My Drive/"
# !cp 'entDict.pickle' "drive/My Drive/"
# !cp 'extDict.pickle' "drive/My Drive"
# !cp 'intDict.pickle' "drive/My Drive"
# !cp 'mechDict.pickle' "drive/My Drive"


In [ ]:
for x in range(len(myCars)):
  #entertainment features
  carFeats=myCars["Entertainment Features"][x].split('^^,')
  for i in range(len(carFeats)):
    carFeats[i]=carFeats[i].replace('^^','')

  carBlob=blobify(carFeats)
  for i in range(len(carBlob)):
    if carBlob[i] in entDict:
      carBlob[i]=entDict[carBlob[i]]

  myCars["Entertainment Features"][x]=list(dict.fromkeys(carBlob))

  #exterior features
  carFeats=myCars["Exterior Features"][x].split('^^,')
  for i in range(len(carFeats)):
    carFeats[i]=carFeats[i].replace('^^','')

  carBlob=blobify(carFeats)
  for i in range(len(carBlob)):
    if carBlob[i] in entDict:
      carBlob[i]=entDict[carBlob[i]]

  myCars["Exterior Features"][x]=list(dict.fromkeys(carBlob))

  #interior features
  carFeats=myCars["Interior Features"][x].split('^^,')
  for i in range(len(carFeats)):
    carFeats[i]=carFeats[i].replace('^^','')

  carBlob=blobify(carFeats)
  for i in range(len(carBlob)):
    if carBlob[i] in entDict:
      carBlob[i]=entDict[carBlob[i]]

  myCars["Interior Features"][x]=list(dict.fromkeys(carBlob))

  #mechanical features
  carFeats=myCars["Mechanical Features"][x].split('^^,')
  for i in range(len(carFeats)):
    carFeats[i]=carFeats[i].replace('^^','')

  carBlob=blobify(carFeats)
  for i in range(len(carBlob)):
    if carBlob[i] in entDict:
      carBlob[i]=entDict[carBlob[i]]

  myCars["Mechanical Features"][x]=list(dict.fromkeys(carBlob))

  #safety features
  carFeats=myCars["Safety Features"][x].split('^^,')
  for i in range(len(carFeats)):
    carFeats[i]=carFeats[i].replace('^^','')

  carBlob=blobify(carFeats)
  for i in range(len(carBlob)):
    if carBlob[i] in entDict:
      carBlob[i]=entDict[carBlob[i]]

  myCars["Safety Features"][x]=list(dict.fromkeys(carBlob))

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  if sys.path[0] == '':
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:48: SettingWithCopyWarning:

In [ ]:
entFeats = [] 
extFeats = []
intFeats = []
mechFeats = []
safeFeats = []


for i in range (0, len(myCars)-1):
  tempFeats = myCars['Entertainment Features'][i]
  entFeats = entFeats + tempFeats

  tempFeats = myCars['Exterior Features'][i]
  extFeats = extFeats + tempFeats
  
  tempFeats = myCars['Interior Features'][i]
  intFeats = intFeats + tempFeats

  tempFeats = myCars['Mechanical Features'][i]
  mechFeats = mechFeats + tempFeats

  tempFeats = myCars['Safety Features'][i]
  safeFeats = safeFeats + tempFeats

When we were doing our machine learning, we accidentally left some of these sections below commented out, effectively removing large portions of the feature data from our data set.  Interestingly, we found that this actually improved the accuracy of our model in some ways.  After trying different combinations, we found that leaving out Mechanical Features produced the best ML models, hence why it is commented out here.

In [ ]:
#one hot encoding entertainment features that atleast 200 cars share
features = []
count=Counter(entFeats)

for x in list(count.keys()):
  if count[x] >= 200:
    features.append(x)
for feat in features:
  lst = np.zeros(2432)
  for i in range(2432):
    if feat in myCars['Entertainment Features'][i]:
      lst[i] = 1
  myCars[feat] = lst

# #one hot encoding cars exterior features over 200 cars share
features = []
count=Counter(extFeats)

for x in list(count.keys()):
  if count[x] >= 200:
    features.append(x)
for feat in features:
  lst = np.zeros(2432)
  for i in range(2432):
    if feat in myCars['Exterior Features'][i]:
      lst[i] = 1
  myCars[feat] = lst


# #one hot encoding cars interior features over 200 cars share
features = []
count=Counter(intFeats)

for x in list(count.keys()):
  if count[x] >= 200:
    features.append(x)
for feat in features:
  lst = np.zeros(2432)
  for i in range(2432):
    if feat in myCars['Interior Features'][i]:
      lst[i] = 1
  myCars[feat] = lst

# # #one hot encoding cars Mechanical features over 200 cars share
# features = []
# count=Counter(mechFeats)

# for x in list(count.keys()):
#   if count[x] >= 200:
#     features.append(x)
# for feat in features:
#   lst = np.zeros(2432)
#   for i in range(2432):
#     if feat in myCars['Mechanical Features'][i]:
#       lst[i] = 1
#   myCars[feat] = lst

# #one hot encoding cars Safety features over 200 cars share
features = []
count=Counter(safeFeats)

for x in list(count.keys()):
  if count[x] >= 200:
    features.append(x)
for feat in features:
  lst = np.zeros(2432)
  for i in range(2432):
    if feat in myCars['Safety Features'][i]:
      lst[i] = 1
  myCars[feat] = lst


In [ ]:
myCars.shape

(2432, 604)

# Dropping and Filling

In [ ]:
myCars =myCars.drop(columns=["Trans Power Take Off",
                             "Trans Description Cont. Again",
                             "Lock to Lock Turns (Steering)",
                             "Lock to Lock Turns (Steering)", 
                             "Unnamed: 0", 
                             "Year",
                             "Transfer Case Gear Ratio (:1), Low",
                             "Cruising Range - City",
                             "Cruising Range - Hwy",
                             "Brake ABS System",
                             "Transfer Case Gear Ratio (:1), High",
                             "Ninth Gear Ratio (:1)",
                             "Tenth Gear Ratio (:1)",
                             "Transfer Case Power Take Off",
                             "Brake ABS System (Second Line)",
                             "Aux Fuel Tank Capacity, Approx",
                             "Steering Ratio (:1), Overall",
                             "Turning Diameter - Wall to Wall",
                             "Fifth Wheel Hitch - Max Trailer Wt.",
                             "Fifth Wheel Hitch - Max Tongue Wt.",
                             "As Spec'd Curb Weight",
                             "Total Option Weight",
                             "Option Weight - Rear",
                             "Option Weight - Front",
                             "Length, Overall w/rear bumper",
                             "Length, Overall w/o rear bumper",
                             "Overhang, Rear w/o bumper",
                             "Cab to End of Frame",
                             "Ext'd Cab Cargo Volume",
                             "Side Door Opening Width",
                             'Entertainment Features',
                             "Exterior Features",
                             "Interior Features",
                             'Mechanical Features',
                             'Safety Features',
                             "Side Door Opening Height",
                             "Side Door Opening Width",
                             "Step Up Height - Front",
                             "Cargo Area Length @ Floor to Console",
                             "Step Up Height - Side",
                             "Processing-Other",
                             "Cargo Volume with Rear Seat Down",
                             "Cargo Volume with Rear Seat Up",
                             "Rear Door Opening Width",
                             "Rear Door Opening Height",
                             "Package",
                             "Exterior Color",
                             "Interior Color",
                             "Spare Wheel Size",
                             "Engine Oil Cooler",
                            "Frame Type",
                            "Drum - Rear (Yes or   )",
                            "Rear Door Type",
                            "Side Door Type",
                            "Ground to Top of Load Floor (in)",
                            "Tailgate Width (in)",
                            "Cargo Box Width @ Top, Rear (in)",
                            "Overhang, Front (in)",
                            "Liftover Height (in)",
                             "Disc - Rear (Yes or   )",
                             "Disc - Front (Yes or   )",
                             "Spare Tire Size",
                             ])

In [ ]:
for x in myCars.columns:
  myCars[x]=myCars[x].fillna(-1)

Through our data exploration we identified some problems with the Horsepower column, some of the car's had -1 values for Horsepower which was very visible when we graphed it. Our first strategy to handle these, was to replace them with values from torque as their values and purpose are very similar, and it's the highest correlating column with Horspower. Unfortunately, all of these cars also had -1's in torque. So, we went and identified these cars and then manually looked up their torque and Horsepower and replaced the -1's with there real value. There where two that didn't have those values released so we decided to drop those two cars, from our data set. These -1's where put into our data in the cleaning notebook inplace of Nan's, after dealing with horsepower and torque, we went back into our cleaning notebook and cleaned up all the other -1's in other columns. We did this by finding the mean of all the positive values in a column and replacing the -1's in a column with that mean. 

Found a zero entry in MSRP, which shouldn't be there so removed it. Considered filling it with msrp average instead, but can't be sure of the completeness of other original data from that row.

In [ ]:

for column in myCars:
  if(pd.api.types.is_numeric_dtype(myCars[column])):
    mask = myCars[column] > 0
    groups = myCars[mask].groupby("Vehicle Type")
    meanRW = myCars[mask][column].mean()

    mask = myCars[column] < 0
    indexes = myCars[mask].index
    if(pd.api.types.is_numeric_dtype(indexes)):
      if (len(indexes) > len(myCars)-1000 ):
        myCars=myCars.drop(columns=column)

for column in myCars:
  if(pd.api.types.is_numeric_dtype(myCars[column])and not(column =="Horsepower") and not(column =="Torque")):
    mask = myCars[column]>0
    vTypes = myCars[mask][["Vehicle Type",column]].groupby("Vehicle Type")
    means=vTypes.mean()
    for i in range(len(myCars[column])):
      if(myCars[column][i]<0):
        try:
          myCars[column][i]=means[myCars["Vehicle Type"][i]]
        except KeyError:
          myCars[column][i]=means.mean()



/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:24: SettingWithCopyWarning: 
A value is trying to b

In [ ]:
#Tesla model 3 AWD
myCars.loc[1372:1373, "Torque (Ft lbs)"] = 471.0
myCars.loc[1372: 1373, "Horsepower"] = 450.0

#Tesla model 3 RWD
myCars.loc[1374, "Torque (Ft lbs)"] = 307.0
myCars.loc[1374, "Horsepower"] = 283.0


#model s specs pulled from https://www.thecarconnection.com/specifications/tesla_model-s_2021
#Tesla model s
myCars.loc[1375:1377, "Torque (Ft lbs)"] = 670.0
myCars.loc[1375:1377, "Horsepower"] = 670.0

myCars.loc[1377:1380, "Torque (Ft lbs)"] = 1020.0
myCars.loc[1377:1380, "Horsepower"] = 1020.0

#model x specs pulled from https://www.tesla.com/modelx
#tesla model x
myCars.loc[1380:1382, "Torque (Ft lbs)"] = 670.0
myCars.loc[1380:1382, "Horsepower"] = 670.0

myCars.loc[1382:1383, "Torque (Ft lbs)"] = 1020.0
myCars.loc[1382:1383, "Horsepower"] = 1020.0

#drop the model y cars
mask = myCars["Horsepower"] < 1
pull = myCars[mask]
myCars = myCars.drop(pull.index)

#Fix the remaining cars with 0 torque values
mask = myCars["Torque (Ft lbs)"] < 1
pull = myCars[mask]
myCars.loc[pull.index, "Torque (Ft lbs)"] = myCars.loc[pull.index, "Horsepower"]

#dropped two cars
mask = myCars["Starting MSRP"] == 0
pull = myCars[mask]
print(pull.index)
myCars = myCars.drop(pull.index)



Int64Index([588, 589], dtype='int64')


# Save CSV

In [ ]:
myCars.to_csv("cleanFeatures.csv",index=False)
!cp cleanFeatures.csv "drive/My Drive/"